In [1]:
pip install ultralytics

INFO: pip is looking at multiple versions of contourpy to determine which version is compatible with other requirements. This could take a while.
   ---------------------------------------- 0.0/1.1 MB ? eta -:--:--
   ---------------------------------------- 1.1/1.1 MB 8.7 MB/s eta 0:00:00
   ---------------------------------------- 0.0/4.3 MB ? eta -:--:--
   --------------------- ------------------ 2.4/4.3 MB 11.2 MB/s eta 0:00:01
   ---------------------------------------- 4.3/4.3 MB 11.2 MB/s eta 0:00:00
   ---------------------------------------- 0.0/109.3 MB ? eta -:--:--
    --------------------------------------- 2.4/109.3 MB 13.4 MB/s eta 0:00:09
   - -------------------------------------- 5.0/109.3 MB 12.6 MB/s eta 0:00:09
   -- ------------------------------------- 7.3/109.3 MB 12.2 MB/s eta 0:00:09
   --- ------------------------------------ 9.7/109.3 MB 12.1 MB/s eta 0:00:09
   ---- ----------------------------------- 12.1/109.3 MB 12.0 MB/s eta 0:00:09
   ----- ----------

In [1]:
import torch
print(torch.cuda.is_available(), torch.cuda.device_count(), torch.version.cuda)

True 1 12.1


In [4]:
from pathlib import Path
print(Path(r"C:\dataset\mealworm\data.yaml").exists())


False


In [7]:
from pathlib import Path
from ultralytics import YOLO

ROOT = Path(r"C:\dataset\mealworm")
img_train = ROOT / "images" / "train"
lbl_train = ROOT / "labels" / "train"

print("[CHECK] images/train:", img_train.exists())
print("[CHECK] labels/train:", lbl_train.exists())
if not img_train.exists() or not lbl_train.exists():
    raise FileNotFoundError("images/train 또는 labels/train 폴더가 없습니다. 경로를 다시 확인해 주세요.")

yaml_path = ROOT / "data.yaml"
if not yaml_path.exists():
    yaml_text = """path: C:/dataset/mealworm
train: images/train
val: images/val   # 아직 val이 없으면 임시로 train 사용
nc: 1
names: [larva]
"""
    yaml_path.write_text(yaml_text, encoding="utf-8")
    print("[MAKE] data.yaml 생성 완료 ->", yaml_path)
else:
    print("[OK] data.yaml 이미 존재 ->", yaml_path)

print("[CHECK] yaml exists:", yaml_path.exists(), "name:", yaml_path.name)
print("[PREVIEW]\n", yaml_path.read_text(encoding="utf-8"))

# ✅ 학습
model = YOLO("yolov8n.pt")
results = model.train(
    data=str(yaml_path),
    epochs=50,
    imgsz=640,
    batch=16,
    device=0,
    workers=4,
    project="runs",
    name="mealworm_detect",
    exist_ok=True,

    # ✅ 추가된 옵션
    save_period=5,   # 5 epoch마다 중간 저장
    save=True,       # 저장 활성화
)


[CHECK] images/train: True
[CHECK] labels/train: True
[OK] data.yaml 이미 존재 -> C:\dataset\mealworm\data.yaml
[CHECK] yaml exists: True name: data.yaml
[PREVIEW]
 path: C:/dataset/mealworm
train: images/train
val: images/val   # 아직 val이 없으면 임시로 train 사용
nc: 1
names: [larva]

Ultralytics 8.3.223  Python-3.10.19 torch-2.5.1+cu121 CUDA:0 (NVIDIA GeForce RTX 3070, 8192MiB)
engine\trainer: agnostic_nms=False, amp=True, augment=False, auto_augment=randaugment, batch=16, bgr=0.0, box=7.5, cache=False, cfg=None, classes=None, close_mosaic=10, cls=0.5, compile=False, conf=None, copy_paste=0.0, copy_paste_mode=flip, cos_lr=False, cutmix=0.0, data=C:\dataset\mealworm\data.yaml, degrees=0.0, deterministic=True, device=0, dfl=1.5, dnn=False, dropout=0.0, dynamic=False, embed=None, epochs=50, erasing=0.4, exist_ok=True, fliplr=0.5, flipud=0.0, format=torchscript, fraction=1.0, freeze=None, half=False, hsv_h=0.015, hsv_s=0.7, hsv_v=0.4, imgsz=640, int8=False, iou=0.7, keras=False, kobj=1.0, line_width=

In [10]:
model.val()


Ultralytics 8.3.223  Python-3.10.19 torch-2.5.1+cu121 CUDA:0 (NVIDIA GeForce RTX 3070, 8192MiB)
val: Fast image access  (ping: 0.10.0 ms, read: 456.9154.4 MB/s, size: 677.1 KB)
val: Scanning C:\dataset\mealworm\labels\val\R_BOX_MB_NM... 6459 images, 0 backgrounds, 1 corrupt: 100% ━━━━━━━━━━━━ 6460/6460 632.3it/s 10.2s<0.0s
val: C:\dataset\mealworm\images\val\R_BOX_MB_UN\R_MB_LV09_UN_20231113_2293.jpg: ignoring corrupt image/label: cannot identify image file 'C:\\dataset\\mealworm\\images\\val\\R_BOX_MB_UN\\R_MB_LV09_UN_20231113_2293.jpg'
val: New cache created: C:\dataset\mealworm\labels\val\R_BOX_MB_NM.cache
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100% ━━━━━━━━━━━━ 404/404 12.0it/s 33.8s<0.1s
                   all       6459      18193      0.978      0.572      0.761      0.729
Speed: 1.3ms preprocess, 1.6ms inference, 0.0ms loss, 0.5ms postprocess per image
Results saved to C:\Users\USER\Desktop\   \script\runs\detect\val4


ultralytics.utils.metrics.DetMetrics object with attributes:

ap_class_index: array([0])
box: ultralytics.utils.metrics.Metric object
confusion_matrix: <ultralytics.utils.metrics.ConfusionMatrix object at 0x0000018F90B08D60>
curves: ['Precision-Recall(B)', 'F1-Confidence(B)', 'Precision-Confidence(B)', 'Recall-Confidence(B)']
curves_results: [[array([          0,    0.001001,    0.002002,    0.003003,    0.004004,    0.005005,    0.006006,    0.007007,    0.008008,    0.009009,     0.01001,    0.011011,    0.012012,    0.013013,    0.014014,    0.015015,    0.016016,    0.017017,    0.018018,    0.019019,     0.02002,    0.021021,    0.022022,    0.023023,
          0.024024,    0.025025,    0.026026,    0.027027,    0.028028,    0.029029,     0.03003,    0.031031,    0.032032,    0.033033,    0.034034,    0.035035,    0.036036,    0.037037,    0.038038,    0.039039,     0.04004,    0.041041,    0.042042,    0.043043,    0.044044,    0.045045,    0.046046,    0.047047,
          0.0480

In [12]:
results = model.predict(
    source=r"C:\dataset\mealworm\images\val\R_BOX_MB_UN\R_MB_LV06_UN_20231025_0015.jpg",  # 테스트할 이미지 경로
    conf=0.5,      # confidence threshold
    save=True,     # 결과 이미지를 자동 저장
    show=True,     # 실행 시 창에 표시 (VSCode 터미널에서는 안보일 수도 있음)
)


image 1/1 C:\dataset\mealworm\images\val\R_BOX_MB_UN\R_MB_LV06_UN_20231025_0015.jpg: 384x640 5 larvas, 14.1ms
Speed: 4.3ms preprocess, 14.1ms inference, 1.6ms postprocess per image at shape (1, 3, 384, 640)
Results saved to C:\Users\USER\Desktop\   \script\runs\detect\predict
